### Ajustaremos los parametros en Vertex AI haciendo uso de hyperparameter_tuning

In [21]:
!python --version

Python 3.9.2


#### El propósito es la implementación de hyperparameter_tuning en la nube
Para definir el modelo por subclassing, el cual recibirá los hiperparámetros
para encontrar los mejores.

In [14]:
!mkdir -p hyper

In [15]:
%%writefile hyper/model.py

import numpy as np
import tensorflow as tf
import os

def hyperparameter_tun(d1,d2,lr,epochs,batch):
    """
    Esta función crea y entrena un modelo utilizando los hiperparámetros proporcionados.

    :param d1: Número de neuronas en la primera capa densa.
    :type d1: int
    :param d2: Número de neuronas en la segunda capa densa.
    :type d2: int
    :param lr: Tasa de aprendizaje para el optimizador Adam.
    :type lr: float
    :param epochs: Número de épocas para entrenar el modelo.
    :type epochs: int
    :param batch: Tamaño del lote para el entrenamiento.
    :type batch: int
    :return: La precisión de validación del modelo entrenado en la última época.
    :rtype: float
    """
    # Subclassing
    class MyModel(tf.keras.Model):  # Hereda de tf.keras.Model.
        def __init__(self, d2):
            super(MyModel, self).__init__()
            self.dense = tf.keras.layers.Dense(d2)

        def call(self, x):
            return self.dense(x)

    class MyModel2(MyModel):  # Hereda de MyModel.
        def __init__(self, d1=10,d2=10):
            super(MyModel2, self).__init__(d2)
            self.dense2 = tf.keras.layers.Dense(d1)
            self.dense3 = tf.keras.layers.Dense(1)

        def call(self, x):
            x = super().call(x)  # Llama al método call de MyModel.
            x = self.dense2(x)
            return self.dense3(x)
        
    model = MyModel2(d1,d2)

    optimizer = tf.keras.optimizers.Adam(learning_rate=lr)
    model.compile(optimizer=optimizer, loss='MSE', metrics=['accuracy'])
    
    x_train = np.random.random((1000, 10))
    y_train = np.random.randint(2, size=(1000,))
    x_val = np.random.random((200, 10))
    y_val = np.random.randint(2, size=(200,))

    history = model.fit(x_train, y_train, epochs=epochs, batch_size=batch, validation_data=(x_val, y_val))

    hp_metric = history.history['val_accuracy'][-1]
    # Evaluar el modelo
    x_test = np.random.random((200, 10))
    y_test = np.random.randint(2, size=(200,))
    evv = model.evaluate(x_test, y_test)
    print("HERE: ",evv)
    model.save('model/m1')
    return hp_metric

Overwriting hyper/model.py


In [16]:
%%writefile hyper/hyper.py

import tensorflow as tf

import google.cloud.aiplatform as aiplatform
from google.cloud.aiplatform import hyperparameter_tuning as hpt
from model import hyperparameter_tun
import argparse
import hypertune

def get_args():
  '''Parses args. Must include all hyperparameters you want to tune.'''

  parser = argparse.ArgumentParser()
  parser.add_argument(
      '--dense1',
      required=True,
      type=int,
      help='dense1')
  parser.add_argument(
      '--dense2',
      required=True,
      type=int,
      help='dense2')
  parser.add_argument(
      '--lr',
      required=True,
      type=float,
      help='learning rate')
  parser.add_argument(
      '--epochs',
      required=True,
      type=int,
      help='epochs')
  parser.add_argument(
      '--batch',
      required=True,
      type=int,
      help='batch')
  args = parser.parse_args()
  return args

def main():
  args = get_args()
  hp_metric = hyperparameter_tun(d1=args.dense1,d2=args.dense2,lr=args.lr,epochs=args.epochs,batch=args.batch)
    
  hpt = hypertune.HyperTune()

  hpt.report_hyperparameter_tuning_metric(
      hyperparameter_metric_tag='accuracy',
      metric_value=hp_metric,
      global_step=args.epochs)


if __name__ == "__main__":
    main()

Overwriting hyper/hyper.py


In [17]:
%%writefile hyper/.dockerignore

__pycache__
*.pyc
*.pyo
*.egg-info
**/model/m0/
**/model/m1/
Dockerfile

env/
.git
.dockerignore
.gitignore

# Jupyter
.ipynb_checkpoints/

# Python
__pycache__/
*.pyc
*.pyo
*.egg-info
*.egg

# Entornos virtuales
venv/
.env/
env
**/__pycache__
__pycache__
*.virtualenv/

# Generales
.DS_Store
*.log
.idea/

Overwriting hyper/.dockerignore


In [18]:
%%writefile hyper/Dockerfile

#FROM gcr.io/deeplearning-platform-release/tf2-gpu.2-8
FROM gcr.io/deeplearning-platform-release/tf-gpu.2-6.py39

WORKDIR /

# Actualiza pip
RUN pip install --upgrade pip
# Copia el archivo requirements.txt al contenedor
COPY requirements.txt /requirements.txt
# Instala las dependencias
RUN pip install -r /requirements.txt
# Installs hypertune library
RUN pip install cloudml-hypertune

# Copies the trainer code to the Docker image.
COPY . .

# Sets up the entry point to invoke the trainer.
ENTRYPOINT ["python", "-m", "hyper"]

Overwriting hyper/Dockerfile


In [23]:
%%bash
source env/bin/activate && pip freeze > hyper/requirements.txt


In [24]:
!docker build -t hyper hyper/

[+] Building 0.0s (0/0)                                          docker:default
[+] Building 0.0s (0/0)                                          docker:default
[+] Building 0.0s (0/0)                                          docker:default
[+] Building 0.0s (0/0)                                          docker:default
[+] Building 0.0s (0/0)                                          docker:default
[+] Building 0.0s (0/0)                                          docker:default
[+] Building 0.0s (0/0)                                          docker:default
[+] Building 0.0s (0/0)                                          docker:default
[+] Building 0.0s (0/0)                                          docker:default
[+] Building 0.0s (0/0)                                          docker:default
[+] Building 0.0s (0/0)                                          docker:default
[+] Building 0.0s (0/0)                                          docker:default
[+] Building 0.0s (0/0)                 

[+] Building 2.3s (2/3)                                          docker:default
 => [internal] load .dockerignore                                          1.4s
 => => transferring context: 349B                                          0.3s
 => [internal] load build definition from Dockerfile                       1.2s
 => => transferring dockerfile: 572B                                       0.1s
 => [internal] load metadata for gcr.io/deeplearning-platform-release/tf-  0.3s
[+] Building 2.4s (2/3)                                          docker:default
 => [internal] load .dockerignore                                          1.4s
 => => transferring context: 349B                                          0.3s
 => [internal] load build definition from Dockerfile                       1.2s
 => => transferring dockerfile: 572B                                       0.1s
 => [internal] load metadata for gcr.io/deeplearning-platform-release/tf-  0.4s
[+] Building 2.6s (2/3)                 

[+] Building 4.5s (4/10)                                         docker:default
 => [internal] load .dockerignore                                          1.4s
 => => transferring context: 349B                                          0.3s
 => [internal] load build definition from Dockerfile                       1.2s
 => => transferring dockerfile: 572B                                       0.1s
 => [internal] load metadata for gcr.io/deeplearning-platform-release/tf-  1.5s
 => [internal] load build context                                          0.2s
 => => transferring context: 28B                                           0.0s
 => [1/7] FROM gcr.io/deeplearning-platform-release/tf-gpu.2-6.py39@sha25  0.0s
[+] Building 4.6s (5/10)                                         docker:default
 => [internal] load .dockerignore                                          1.4s
 => => transferring context: 349B                                          0.3s
 => [internal] load build definition fro

[+] Building 5.8s (6/10)                                         docker:default
 => [internal] load .dockerignore                                          1.4s
 => => transferring context: 349B                                          0.3s
 => [internal] load build definition from Dockerfile                       1.2s
 => => transferring dockerfile: 572B                                       0.1s
 => [internal] load metadata for gcr.io/deeplearning-platform-release/tf-  1.5s
 => [internal] load build context                                          0.3s
 => => transferring context: 4.66kB                                        0.0s
 => [1/7] FROM gcr.io/deeplearning-platform-release/tf-gpu.2-6.py39@sha25  0.0s
 => CACHED [2/7] RUN pip install --upgrade pip                             0.0s
 => [3/7] COPY requirements.txt /requirements.txt                          1.2s
[+] Building 6.0s (6/10)                                         docker:default
 => [internal] load .dockerignore       

[+] Building 7.0s (7/10)                                         docker:default
 => [internal] load .dockerignore                                          1.4s
 => => transferring context: 349B                                          0.3s
 => [internal] load build definition from Dockerfile                       1.2s
 => => transferring dockerfile: 572B                                       0.1s
 => [internal] load metadata for gcr.io/deeplearning-platform-release/tf-  1.5s
 => [internal] load build context                                          0.3s
 => => transferring context: 4.66kB                                        0.0s
 => [1/7] FROM gcr.io/deeplearning-platform-release/tf-gpu.2-6.py39@sha25  0.0s
 => CACHED [2/7] RUN pip install --upgrade pip                             0.0s
 => [3/7] COPY requirements.txt /requirements.txt                          1.5s
 => [4/7] RUN pip install -r /requirements.txt                             0.7s
[+] Building 7.2s (7/10)                

...

[+] Building 678.0s (11/11)                                      docker:default
 => [internal] load .dockerignore                                          1.4s
 => => transferring context: 349B                                          0.3s
 => [internal] load build definition from Dockerfile                       1.2s
 => => transferring dockerfile: 572B                                       0.1s
 => [internal] load metadata for gcr.io/deeplearning-platform-release/tf-  1.5s
 => [internal] load build context                                          0.3s
 => => transferring context: 4.66kB                                        0.0s
 => [1/7] FROM gcr.io/deeplearning-platform-release/tf-gpu.2-6.py39@sha25  0.0s
 => CACHED [2/7] RUN pip install --upgrade pip                             0.0s
 => [3/7] COPY requirements.txt /requirements.txt                          1.5s
 => [4/7] RUN pip install -r /requirements.txt                           583.3s
 => [5/7] RUN pip install cloudml-hypert

[+] Building 678.8s (11/11)                                      docker:default
 => [internal] load .dockerignore                                          1.4s
 => => transferring context: 349B                                          0.3s
 => [internal] load build definition from Dockerfile                       1.2s
 => => transferring dockerfile: 572B                                       0.1s
 => [internal] load metadata for gcr.io/deeplearning-platform-release/tf-  1.5s
 => [internal] load build context                                          0.3s
 => => transferring context: 4.66kB                                        0.0s
 => [1/7] FROM gcr.io/deeplearning-platform-release/tf-gpu.2-6.py39@sha25  0.0s
 => CACHED [2/7] RUN pip install --upgrade pip                             0.0s
 => [3/7] COPY requirements.txt /requirements.txt                          1.5s
 => [4/7] RUN pip install -r /requirements.txt                           583.3s
 => [5/7] RUN pip install cloudml-hypert

[+] Building 679.6s (11/11)                                      docker:default
 => [internal] load .dockerignore                                          1.4s
 => => transferring context: 349B                                          0.3s
 => [internal] load build definition from Dockerfile                       1.2s
 => => transferring dockerfile: 572B                                       0.1s
 => [internal] load metadata for gcr.io/deeplearning-platform-release/tf-  1.5s
 => [internal] load build context                                          0.3s
 => => transferring context: 4.66kB                                        0.0s
 => [1/7] FROM gcr.io/deeplearning-platform-release/tf-gpu.2-6.py39@sha25  0.0s
 => CACHED [2/7] RUN pip install --upgrade pip                             0.0s
 => [3/7] COPY requirements.txt /requirements.txt                          1.5s
 => [4/7] RUN pip install -r /requirements.txt                           583.3s
 => [5/7] RUN pip install cloudml-hypert

[+] Building 680.3s (11/11)                                      docker:default
 => [internal] load .dockerignore                                          1.4s
 => => transferring context: 349B                                          0.3s
 => [internal] load build definition from Dockerfile                       1.2s
 => => transferring dockerfile: 572B                                       0.1s
 => [internal] load metadata for gcr.io/deeplearning-platform-release/tf-  1.5s
 => [internal] load build context                                          0.3s
 => => transferring context: 4.66kB                                        0.0s
 => [1/7] FROM gcr.io/deeplearning-platform-release/tf-gpu.2-6.py39@sha25  0.0s
 => CACHED [2/7] RUN pip install --upgrade pip                             0.0s
 => [3/7] COPY requirements.txt /requirements.txt                          1.5s
 => [4/7] RUN pip install -r /requirements.txt                           583.3s
 => [5/7] RUN pip install cloudml-hypert

[+] Building 681.1s (11/11)                                      docker:default
 => [internal] load .dockerignore                                          1.4s
 => => transferring context: 349B                                          0.3s
 => [internal] load build definition from Dockerfile                       1.2s
 => => transferring dockerfile: 572B                                       0.1s
 => [internal] load metadata for gcr.io/deeplearning-platform-release/tf-  1.5s
 => [internal] load build context                                          0.3s
 => => transferring context: 4.66kB                                        0.0s
 => [1/7] FROM gcr.io/deeplearning-platform-release/tf-gpu.2-6.py39@sha25  0.0s
 => CACHED [2/7] RUN pip install --upgrade pip                             0.0s
 => [3/7] COPY requirements.txt /requirements.txt                          1.5s
 => [4/7] RUN pip install -r /requirements.txt                           583.3s
 => [5/7] RUN pip install cloudml-hypert

In [25]:
!docker tag hyper us-central1-docker.pkg.dev/projecto2-373519/myimages/hyper:v1.0.0

In [26]:
!docker push us-central1-docker.pkg.dev/projecto2-373519/myimages/hyper:v1.0.0

The push refers to repository [us-central1-docker.pkg.dev/projecto2-373519/myimages/hyper]

c9e90d8e: Preparing 
85932949: Preparing 
7963e1db: Preparing 
180ff4a4: Preparing 
78a248f7: Preparing 
b226dce7: Preparing 
c4965b5e: Preparing 
25e72d8c: Preparing 
fdd637a6: Preparing 
1baf85b7: Preparing 
03debd52: Waiting g 
a94acbc6: Preparing 
b0d58883: Waiting g 
823e41c0: Preparing 
15a0379c: Preparing 
132bdfac: Preparing 
61c403d2: Preparing 
77448bdb: Waiting g 
c0615eca: Preparing 
d691ddb5: Waiting g 
af416cd0: Preparing 
e84d418f: Preparing 
121f673a: Preparing 
c96b1709: Preparing 
c46fbfad: Preparing 
453446cc: Preparing 
8dc4d7e3: Preparing 
00d600a0: Preparing 
bf18a086: Preparing 
e86e231e: Waiting g 
ea0ea8d8: Preparing 
ad0ce3ec: Preparing 
17453a10: Preparing 
e1a1cbfb: Preparing 
7090d6d6: Preparing 
ea0ea8d8: Waiting g 
ef4e19ae: Preparing 
7090d6d6: Waiting g 
1fa7f0e3: Waiting g 
7a859620: Preparing 
183bef21: Preparing 
69562af2: Preparing 


963e1db: Pushing  2.053GB/2.234GB

963e1db: Pushed   2.252GB/2.234GBv1.0.0: digest: sha256:474f5615c981c0a0fa7482b02a62f3feaf8679a6a83590d990d1fbccb3bccdac size: 9336


# Configurando Hiperparametros

In [2]:
import google.cloud.aiplatform as aiplatform
from google.cloud.aiplatform import hyperparameter_tuning as hpt

In [13]:
!gcloud auth application-default login

Your browser has been opened to visit:

    https://accounts.google.com/o/oauth2/auth?response_type=code&client_id=764086051850-6qr4p6gpi6hn506pt8ejuq83di341hur.apps.googleusercontent.com&redirect_uri=http%3A%2F%2Flocalhost%3A8085%2F&scope=openid+https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fuserinfo.email+https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fcloud-platform+https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fsqlservice.login&state=3rLZh5nlXp4EWk0GL7b6SNW1S8A0uG&access_type=offline&code_challenge=cw4EW0S5GV0HCGUiWDqybVdiTAtON3-zqJx6ZAM_oS4&code_challenge_method=S256


Credentials saved to file: [/home/eyes/.config/gcloud/application_default_credentials.json]

These credentials will be used by any library that requests Application Default Credentials (ADC).

Quota project "projecto2-373519" was added to ADC which can be used by Google client libraries for billing and quota. Note that some services may still bill the project owning the resource.


In [14]:
aiplatform.init(location="us-central1")

In [19]:
worker_pool_specs = [
    {
        "machine_spec": {
            "machine_type": "n1-standard-4",
            "accelerator_type": None, #"NVIDIA_TESLA_T4",
            "accelerator_count": None,
        },
        "replica_count": 1,
        "container_spec": {
            "image_uri": "us-central1-docker.pkg.dev/projecto2-373519/myimages/hyper:v1.0.0"
        },
    }
]

In [23]:
my_custom_job = aiplatform.CustomJob(
    display_name="tunning",
    worker_pool_specs=worker_pool_specs,
    staging_bucket="gs://models_ai_save_2/tunning",
)

In [24]:
metric_spec = {"accuracy": "maximize"}
parameter_spec = {
    "dense1": hpt.DiscreteParameterSpec(values=[5, 6], scale=None),
    "dense2": hpt.DiscreteParameterSpec(values=[4, 5, 6], scale=None),
    "lr": hpt.DoubleParameterSpec(min=0.001, max=1, scale="log"),
    "epochs": hpt.DiscreteParameterSpec(values=[2, 3, 4], scale=None),
    "batch": hpt.DiscreteParameterSpec(values=[8, 16, 32], scale=None),
}

In [25]:
hp_job = aiplatform.HyperparameterTuningJob(
    display_name="tunning_params",
    custom_job=my_custom_job,
    metric_spec=metric_spec,
    parameter_spec=parameter_spec,
    max_trial_count=3,
    parallel_trial_count=3,
)

hp_job.run()

Creating HyperparameterTuningJob
HyperparameterTuningJob created. Resource name: projects/936401695274/locations/us-central1/hyperparameterTuningJobs/4028515290257031168
To use this HyperparameterTuningJob in another session:
hpt_job = aiplatform.HyperparameterTuningJob.get('projects/936401695274/locations/us-central1/hyperparameterTuningJobs/4028515290257031168')
View HyperparameterTuningJob:
https://console.cloud.google.com/ai/platform/locations/us-central1/training/4028515290257031168?project=936401695274
HyperparameterTuningJob projects/936401695274/locations/us-central1/hyperparameterTuningJobs/4028515290257031168 current state:
JobState.JOB_STATE_PENDING
HyperparameterTuningJob projects/936401695274/locations/us-central1/hyperparameterTuningJobs/4028515290257031168 current state:
JobState.JOB_STATE_RUNNING
HyperparameterTuningJob projects/936401695274/locations/us-central1/hyperparameterTuningJobs/4028515290257031168 current state:
JobState.JOB_STATE_RUNNING
HyperparameterTuningJ

HyperparameterTuningJob projects/936401695274/locations/us-central1/hyperparameterTuningJobs/4028515290257031168 current state:
JobState.JOB_STATE_RUNNING
HyperparameterTuningJob projects/936401695274/locations/us-central1/hyperparameterTuningJobs/4028515290257031168 current state:
JobState.JOB_STATE_RUNNING
HyperparameterTuningJob projects/936401695274/locations/us-central1/hyperparameterTuningJobs/4028515290257031168 current state:
JobState.JOB_STATE_RUNNING
HyperparameterTuningJob projects/936401695274/locations/us-central1/hyperparameterTuningJobs/4028515290257031168 current state:
JobState.JOB_STATE_RUNNING
HyperparameterTuningJob projects/936401695274/locations/us-central1/hyperparameterTuningJobs/4028515290257031168 current state:
JobState.JOB_STATE_RUNNING
HyperparameterTuningJob projects/936401695274/locations/us-central1/hyperparameterTuningJobs/4028515290257031168 current state:
JobState.JOB_STATE_RUNNING
HyperparameterTuningJob projects/936401695274/locations/us-central1/hy

HyperparameterTuningJob projects/936401695274/locations/us-central1/hyperparameterTuningJobs/4028515290257031168 current state:
JobState.JOB_STATE_RUNNING
HyperparameterTuningJob projects/936401695274/locations/us-central1/hyperparameterTuningJobs/4028515290257031168 current state:
JobState.JOB_STATE_RUNNING
HyperparameterTuningJob projects/936401695274/locations/us-central1/hyperparameterTuningJobs/4028515290257031168 current state:
JobState.JOB_STATE_RUNNING
HyperparameterTuningJob projects/936401695274/locations/us-central1/hyperparameterTuningJobs/4028515290257031168 current state:
JobState.JOB_STATE_RUNNING
HyperparameterTuningJob projects/936401695274/locations/us-central1/hyperparameterTuningJobs/4028515290257031168 current state:
JobState.JOB_STATE_RUNNING
HyperparameterTuningJob projects/936401695274/locations/us-central1/hyperparameterTuningJobs/4028515290257031168 current state:
JobState.JOB_STATE_RUNNING
HyperparameterTuningJob projects/936401695274/locations/us-central1/hy

# FIN